In [5]:
import pandas as pd
import numpy as np
import glob
import xarray as xr

idx = pd.IndexSlice

_thudohanoi_data_path = r'/mnt/4ba37af6-51fd-47bc-8321-8c500c229114/study/School/KHOA LUAN TOT NGHIEP/Data/thudohanoi'
_thudohanoi_files = glob.glob(_thudohanoi_data_path + '/*.csv')

In [6]:
# Currently all data are ug/m3 so we doesn't need to converse them.
thudohanoi_df = pd.DataFrame()
for file in _thudohanoi_files:
    thudohanoi_df = thudohanoi_df.append(pd.read_csv(file, parse_dates=True, index_col=['site_id', 'time']))
thudohanoi_df = thudohanoi_df.rename(columns={"PM2.5": "PM25"})

In [7]:
#https://vanbanphapluat.co/quyet-dinh-1459-qd-tcmt-2019-ky-thuat-tinh-toan-va-cong-bo-chi-so-chat-luong-khong-khi-viet-nam
def create_BP_df():
    BP_Ii = [0,50,100,150,200,300,400,500]
    BP_O3_1h = [0,160,200,300,400,800,1000,1200]
    BP_O3_8h = [0,120,170,210,400]
    BP_CO = [0,10000,30000,45000,60000,90000,120000,150000]
    BP_SO2 = [0,125,350,550,800,1600,2100,2630]
    BP_NO2 = [0,100,200,700,1200,2350,3100,3850]
    BP_PM10 = [0,50,150,250,350,420,500,600]
    BP_PM25 = [0,25,50,80,150,250,350,500]
    BP = pd.DataFrame(data = [range(1,9),BP_Ii, BP_O3_1h, BP_O3_8h, BP_CO, BP_SO2, BP_NO2, BP_PM10, BP_PM25],
                      index=['I','Ii','O3','O3_8h','CO','SO2','NO2','PM10','PM25'], dtype= np.int64)
    BP = BP.transpose().set_index('I')
    #Add a upper to calculate I = 8
    BP.loc[9] = [999999,999999,999999,999999,999999,999999,999999,999999]
    BP.index = BP.index.astype(np.int64)
    return BP
_global_BP = create_BP_df()

In [8]:
#Cho vao bang BP, series gia tri 5 hop chat
#Dau ra la 1 series gom co gia tri index cua 5 hop chat do
#Dau ra lan luot cua cac chat [CO, NO2, O3, PM25, SO2]
def calculate_BP_I(polutant_data, BP = create_BP_df()):
    result_I = []
    BP_polutant_column = BP.loc[:,polutant_data.name]
    result_I = polutant_data.apply(lambda x: BP_polutant_column.ge(x).idxmax() - 1)
#     print(polutant_data)
    return result_I
sample_series = thudohanoi_df
sample_series = sample_series.apply(lambda x: calculate_BP_I(x,_global_BP), axis=0, result_type = 'broadcast')
# sample_result = pd.DataFrame(sample_result, index=['lat', 'lon', 'time'])

In [10]:
#Cong thuc tinh duoc lay tu duong link nay: 
#http://tapchimoitruong.vn/pages/article.aspx?item=New-calculation-of-the-Vi%E1%BB%87t-Nam-Air-Quality-Index-51306
#http://cem.gov.vn/storage/news_file_attach/QD%201459%20TCMT%20ngay%2012.11.2019%20AQI.pdf
#Cong thuc nay se lay input la 1 dataframe so do hop chat cho output ra 1 series gom so AQI cua moi gio (Lon nhat trong tat ca hop chat)
def calculate_AQI_h(data = None, formular = 1):  
    #Cong thuc 1 = ((Ii[i+1] - Ii[i])/ (BP[i+1] - BP[i]))* (C[h] - BP[i]) +Ii[i]
    def calculate_AQI_formular(polutant_data, I, BP = _global_BP):
        result = []
        for data in zip(polutant_data.index, polutant_data.values, I.values):
            polutant_name, polutant_value, I = data
            I = int(I)
            try:
                AQI = ((BP.loc[I + 1,'Ii'] - BP.loc[I, 'Ii']) / (BP.loc[I+1, polutant_name] - BP.loc[I, polutant_name])
                                                   * (polutant_value - BP.loc[I, polutant_name])) + BP.loc[I, 'Ii']
            except KeyError:
                print(data)
                if I == 0:
                    AQI = 0
                else:
                    AQI = 500
            result.append(AQI)
        return result
    
    #VietNam system use 12 hours for nowcast, the current hour and 11 hours before.
    def nowcast(polutant_data, element):
        site_id, time = element.name
            #Nhung cong viec can lam
            #Get data for the hour and 12 hours behind it in the same spot
        tmp_12h_data_storage = polutant_data.loc[
            idx[site_id, time - pd.Timedelta(hours=12) : time]]
            #Kiem tra xem trong 3 gio gan nhat thi it nhat 2 gio phai co so lieu
            #Neu khong qua duoc check o tren thi so lieu tinh duoc dat la np.nan
        if tmp_12h_data_storage.iloc[:3].isna().sum() > 2:
            result = np.nan
        elif len(tmp_12h_data_storage) < 4:
            result = np.nan
        else:
            #Trong 12 gia tri do lay gia tri min va max
            min_data = tmp_12h_data_storage.min()
            max_data = tmp_12h_data_storage.max()
            #Tinh Weight bang cach lay gia tri lon nhat chia gia tri nho
            try:
                w = min_data / max_data
            except ZeroDivisionError:
                print(site_id, time)
            #Neu weight < 1/2 thi dat weight = 1/2
            if w < 1/2:
                w = 1/2
            #Tinh gia tri nowcast dua theo cong thuc
            nowcast = sum([(w**i) * tmp_12h_data_storage.iloc[i-1] for i in range(1,len(tmp_12h_data_storage)+1)]) / sum([(w**i) for i in range(1,len(tmp_12h_data_storage) + 1)])
            #Add gia tri now cast vao ket qua tra ve
            result = nowcast
            print(tmp_12h_data_storage)
        return result
    #Init variable
    idx = pd.IndexSlice
    #Sort index to slice
    data.sort_index(level=['site_id', 'time'], ascending=[1,1], inplace=True)
    
    #Air index number of all polutant data
    
    data.loc[:,['PM25']] = data.loc[:,['PM25']].apply((lambda x: nowcast(data.loc[:,'PM25'], x)), axis=1, result_type='broadcast')
    I_number = data.apply((lambda x: calculate_BP_I(x, _global_BP)), axis=0, result_type='broadcast')
    
    calculated_AQI = I_number.apply((lambda x: calculate_AQI_formular(data.loc[x.name, :], x, _global_BP)),
                                axis=1, result_type='broadcast')
    calculated_AQI['AQI_h'] = calculated_AQI.max(axis=1)
    calculated_AQI['AQI_h_Polutant'] = calculated_AQI.idxmax(axis=1)
    calculated_AQI['AQI_h_I'] = I_number.max(axis=1)  
    return calculated_AQI
AQI = calculate_AQI_h(thudohanoi_df)

site_id  time               
1        2020-12-05 00:00:00    33.7
         2020-12-05 01:00:00    32.3
         2020-12-05 02:00:00    25.2
         2020-12-05 03:00:00    20.6
Name: PM25, dtype: float64
site_id  time               
1        2020-12-05 00:00:00    33.7
         2020-12-05 01:00:00    32.3
         2020-12-05 02:00:00    25.2
         2020-12-05 03:00:00    20.6
         2020-12-05 04:00:00    29.8
Name: PM25, dtype: float64
site_id  time               
1        2020-12-05 00:00:00    33.7
         2020-12-05 01:00:00    32.3
         2020-12-05 02:00:00    25.2
         2020-12-05 03:00:00    20.6
         2020-12-05 04:00:00    29.8
         2020-12-05 05:00:00    27.8
Name: PM25, dtype: float64
site_id  time               
1        2020-12-05 00:00:00    33.7
         2020-12-05 01:00:00    32.3
         2020-12-05 02:00:00    25.2
         2020-12-05 03:00:00    20.6
         2020-12-05 04:00:00    29.8
         2020-12-05 05:00:00    27.8
         2020-12-05 06:00:

site_id  time               
1        2020-12-07 10:00:00    47.1
         2020-12-07 11:00:00    51.6
         2020-12-07 12:00:00    52.5
         2020-12-07 13:00:00    47.8
         2020-12-07 14:00:00    45.3
         2020-12-07 15:00:00    46.6
         2020-12-07 16:00:00    67.2
         2020-12-07 17:00:00    73.0
         2020-12-07 18:00:00    61.8
         2020-12-07 19:00:00    63.1
         2020-12-07 20:00:00    58.3
         2020-12-07 21:00:00    59.6
         2020-12-07 22:00:00    68.3
Name: PM25, dtype: float64
site_id  time               
1        2020-12-07 11:00:00    51.6
         2020-12-07 12:00:00    52.5
         2020-12-07 13:00:00    47.8
         2020-12-07 14:00:00    45.3
         2020-12-07 15:00:00    46.6
         2020-12-07 16:00:00    67.2
         2020-12-07 17:00:00    73.0
         2020-12-07 18:00:00    61.8
         2020-12-07 19:00:00    63.1
         2020-12-07 20:00:00    58.3
         2020-12-07 21:00:00    59.6
         2020-12-07 22:00:0

site_id  time               
1        2020-12-10 05:00:00    60.3
         2020-12-10 06:00:00    52.7
         2020-12-10 07:00:00    50.7
         2020-12-10 08:00:00    64.3
         2020-12-10 09:00:00    58.0
         2020-12-10 10:00:00    53.8
         2020-12-10 11:00:00    48.6
         2020-12-10 12:00:00    39.2
         2020-12-10 13:00:00    44.4
         2020-12-10 14:00:00    36.8
         2020-12-10 15:00:00    43.6
         2020-12-10 16:00:00    48.8
         2020-12-10 17:00:00    50.7
Name: PM25, dtype: float64
site_id  time               
1        2020-12-10 06:00:00    52.7
         2020-12-10 07:00:00    50.7
         2020-12-10 08:00:00    64.3
         2020-12-10 09:00:00    58.0
         2020-12-10 10:00:00    53.8
         2020-12-10 11:00:00    48.6
         2020-12-10 12:00:00    39.2
         2020-12-10 13:00:00    44.4
         2020-12-10 14:00:00    36.8
         2020-12-10 15:00:00    43.6
         2020-12-10 16:00:00    48.8
         2020-12-10 17:00:0

site_id  time               
1        2020-12-12 18:00:00    49.1
         2020-12-12 19:00:00    59.2
         2020-12-12 20:00:00    59.4
         2020-12-12 21:00:00    63.6
         2020-12-12 22:00:00    70.7
         2020-12-12 23:00:00    79.8
         2020-12-13 00:00:00    71.1
         2020-12-13 01:00:00    59.8
         2020-12-13 02:00:00    62.3
         2020-12-13 03:00:00    61.6
         2020-12-13 04:00:00    62.1
         2020-12-13 05:00:00    69.5
         2020-12-13 06:00:00    72.8
Name: PM25, dtype: float64
site_id  time               
1        2020-12-12 19:00:00    59.2
         2020-12-12 20:00:00    59.4
         2020-12-12 21:00:00    63.6
         2020-12-12 22:00:00    70.7
         2020-12-12 23:00:00    79.8
         2020-12-13 00:00:00    71.1
         2020-12-13 01:00:00    59.8
         2020-12-13 02:00:00    62.3
         2020-12-13 03:00:00    61.6
         2020-12-13 04:00:00    62.1
         2020-12-13 05:00:00    69.5
         2020-12-13 06:00:0

site_id  time               
1        2020-12-15 05:00:00    41.3
         2020-12-15 06:00:00    30.9
         2020-12-15 07:00:00    20.2
         2020-12-15 08:00:00    18.5
         2020-12-15 09:00:00    16.0
         2020-12-15 10:00:00    12.8
         2020-12-15 11:00:00    15.7
         2020-12-15 12:00:00    29.1
         2020-12-15 13:00:00    35.5
         2020-12-15 14:00:00    36.6
         2020-12-15 15:00:00    31.2
         2020-12-15 16:00:00    29.7
         2020-12-15 17:00:00    33.7
Name: PM25, dtype: float64
site_id  time               
1        2020-12-15 06:00:00    30.9
         2020-12-15 07:00:00    20.2
         2020-12-15 08:00:00    18.5
         2020-12-15 09:00:00    16.0
         2020-12-15 10:00:00    12.8
         2020-12-15 11:00:00    15.7
         2020-12-15 12:00:00    29.1
         2020-12-15 13:00:00    35.5
         2020-12-15 14:00:00    36.6
         2020-12-15 15:00:00    31.2
         2020-12-15 16:00:00    29.7
         2020-12-15 17:00:0

...

site_id  time               
16       2020-12-07 00:00:00     72.32
         2020-12-07 01:00:00     66.85
         2020-12-07 02:00:00     72.41
         2020-12-07 03:00:00     75.60
         2020-12-07 04:00:00     95.02
         2020-12-07 05:00:00    131.05
         2020-12-07 06:00:00    144.04
         2020-12-07 07:00:00    100.96
         2020-12-07 08:00:00     95.88
         2020-12-07 09:00:00     90.50
         2020-12-07 10:00:00     86.19
         2020-12-07 11:00:00     79.01
         2020-12-07 12:00:00     78.68
Name: PM25, dtype: float64
site_id  time               
16       2020-12-07 01:00:00     66.85
         2020-12-07 02:00:00     72.41
         2020-12-07 03:00:00     75.60
         2020-12-07 04:00:00     95.02
         2020-12-07 05:00:00    131.05
         2020-12-07 06:00:00    144.04
         2020-12-07 07:00:00    100.96
         2020-12-07 08:00:00     95.88
         2020-12-07 09:00:00     90.50
         2020-12-07 10:00:00     86.19
         2020-12-0

site_id  time               
16       2020-12-09 18:00:00     69.92
         2020-12-09 19:00:00     63.52
         2020-12-09 20:00:00     83.75
         2020-12-09 21:00:00     88.13
         2020-12-09 22:00:00     82.39
         2020-12-09 23:00:00     84.09
         2020-12-10 00:00:00     79.87
         2020-12-10 01:00:00     62.32
         2020-12-10 02:00:00     62.56
         2020-12-10 03:00:00     65.43
         2020-12-10 04:00:00     80.76
         2020-12-10 05:00:00    125.29
         2020-12-10 06:00:00    137.87
Name: PM25, dtype: float64
site_id  time               
16       2020-12-09 19:00:00     63.52
         2020-12-09 20:00:00     83.75
         2020-12-09 21:00:00     88.13
         2020-12-09 22:00:00     82.39
         2020-12-09 23:00:00     84.09
         2020-12-10 00:00:00     79.87
         2020-12-10 01:00:00     62.32
         2020-12-10 02:00:00     62.56
         2020-12-10 03:00:00     65.43
         2020-12-10 04:00:00     80.76
         2020-12-1

site_id  time               
16       2020-12-12 07:00:00     76.85
         2020-12-12 08:00:00     94.80
         2020-12-12 09:00:00     97.33
         2020-12-12 10:00:00    108.00
         2020-12-12 11:00:00    122.07
         2020-12-12 12:00:00    114.70
         2020-12-12 13:00:00    102.83
         2020-12-12 14:00:00     88.35
         2020-12-12 15:00:00     75.00
         2020-12-12 16:00:00     64.85
         2020-12-12 17:00:00     63.25
         2020-12-12 18:00:00     64.18
         2020-12-12 19:00:00     55.69
Name: PM25, dtype: float64
site_id  time               
16       2020-12-12 08:00:00     94.80
         2020-12-12 09:00:00     97.33
         2020-12-12 10:00:00    108.00
         2020-12-12 11:00:00    122.07
         2020-12-12 12:00:00    114.70
         2020-12-12 13:00:00    102.83
         2020-12-12 14:00:00     88.35
         2020-12-12 15:00:00     75.00
         2020-12-12 16:00:00     64.85
         2020-12-12 17:00:00     63.25
         2020-12-1

site_id  time               
16       2020-12-13 16:00:00    45.88
         2020-12-13 17:00:00    37.83
         2020-12-13 18:00:00    33.38
         2020-12-13 19:00:00    26.44
         2020-12-13 20:00:00    33.20
         2020-12-13 21:00:00    59.20
         2020-12-13 22:00:00    80.08
         2020-12-13 23:00:00    86.14
         2020-12-14 00:00:00    71.83
         2020-12-14 01:00:00    53.17
         2020-12-14 02:00:00    58.93
         2020-12-14 03:00:00    63.26
         2020-12-14 04:00:00    68.52
Name: PM25, dtype: float64
site_id  time               
16       2020-12-13 17:00:00    37.83
         2020-12-13 18:00:00    33.38
         2020-12-13 19:00:00    26.44
         2020-12-13 20:00:00    33.20
         2020-12-13 21:00:00    59.20
         2020-12-13 22:00:00    80.08
         2020-12-13 23:00:00    86.14
         2020-12-14 00:00:00    71.83
         2020-12-14 01:00:00    53.17
         2020-12-14 02:00:00    58.93
         2020-12-14 03:00:00    63.26
   

UnboundLocalError: local variable 'w' referenced before assignment

In [ ]:
# '''Lam 4 model:
# Random forest
# gradient boosting regression
# decision tree regression
# mlp regression'''

import numpy as np
from sklearn import datasets
from sklearn.datasets import make_moons
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import PolynomialFeatures
from sklearn.preprocessing import StandardScaler
from sklearn.svm import LinearSVC

from sklearn.ensemble import RandomForestRegressor
from sklearn.model_selection import train_test_split

moon_dataset = make_moons(1000, noise = 0.4)
X = moon_dataset[0]
y = moon_dataset[1]

rnd_clf = RandomForestRegressor(n_estimators = 500, max_leaf_nodes = 16, n_jobs = -1)
X_train, X_test, y_train, y_test = train_test_split(X, y, random_state = 0)

rnd_clf.fit(X_train, y_train)


In [ ]:
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.metrics import mean_squared_error

gbrt = GradientBoostingRegressor(max_depth = 2, n_estimators=3, learning_rate = 1.0)
gbrt.fit(X_train, y_train)

#measure the validation error at each stage of training to find the optimal number of trees

errors = [mean_squared_error(y_val, y_pred)
         for y_pred in gbrt.staged_predict(X_val)]
bst_n_estimators = np.argmin(errors)

gbrt_best = GradientBoostingRegressor(max_depth = 2, n_estimators = bst_n_estimators)
gbrt_best.fit(X_train, y_train)

In [ ]:
from sklearn.model_selection import cross_val_score
from sklearn.tree import DecisionTreeRegressor

decision_tree_reg = DecisionTreeRegressor(random_state = 0)
cross_val_score(decision_tree_reg, X_train, y_train, cv = 10)

In [ ]:
from sklearn.neural_network import MLPRegressor
from sklearn.model_selection import train_test_split

mlp_reg = MLPRegressor(random_state=0, max_iter=500).fit(X_train, y_train)

mlp_reg.score(X_test, y_test)